Import the preprepared dataset, indexed by system_metadata_id, and renaming columns to replace the '.' with _ to avoid later errors.

In [1]:
import requests
from urllib import parse
from pprint import pprint
import pandas as pd
import config
import numpy as np
import os, sys

pd.set_option('display.max_rows', None)


if not os.path.exists('data/cleaned_opendoar_data.csv'):
    print('data/cleaned_opendoar_data.csv doesnt exist, please run international_opendoar.py to create it.')
    sys.exit()

input_data = 'data/cleaned_opendoar_data.csv'
df_all_data = pd.read_csv(input_data, header=0)
df_all_data.columns=df_all_data.columns.str.replace('.','_')
#df_all_data.set_index('system_metadata_id', inplace=True)

display(df_all_data)

 

/tmp/ipykernel_93435/1805871215.py:18: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df_all_data.columns=df_all_data.columns.str.replace('.','_')


system_metadata_id organisation_country  \
0                      2                   ch   
1                      3                   it   
2                      5                   gb   
3                      7                   fr   
4                      8                   fr   
5                     10                   fr   
6                     13                   de   
7                     17                   au   
8                     24                   no   
9                     25                   co   
10                    26                   br   
11                    30                   gb   
12                    35                   it   
13                    38                   us   
14                    40                   us   
15                    54                   gb   
16                    55                   gb   
17                    57                   gb   
18                    58                   fr   
19                    59                   fr   
20                    61                   us   
21                    63                   hu   
22                    64                   hu   
23                    66                   fr   
24                    69                   us   
25                    70                   gb   
26                    72                   jp   
27                    73                   au   
28                    76                   se   
29                    79                   au   
30                    80                   fr   
31                    83                   nl   
32                    84                   us   
33                    85                   us   
34                    87                   us   
35                    88                   us   
36                    91                   us   
37                    93                   us   
38                    94                   us   
39                    96                   us   
40                    98                   us   
41                    99                   us   
42                   100                   us   
43                   101                   nl   
44                   104                   de   
45                   105                   be   
46                   108                   us   
47                   109                   gb   
48                   114                   cl   
49                   115                   in   
50                   116                   in   
51                   117                   jp   
52                   119                   ie   
53                   121                   no   
54                   126                   es   
55                   128                   gb   
56                   130                   us   
57                   131                   ca   
58                   133                   de   
59                   134                   de   
60                   135                   se   
61                   137                   us   
62                   138                   us   
63                   139                   de   
64                   142                   se   
65                   145                   us   
66                   146                   us   
67                   147                   us   
68                   148                   us   
69                   149                   in   
70                   150                   ch   
71                   151                   it   
72                   152                   it   
73                   153                   us   
74                   156                   de   
75                   157                   us   
76                   162                   gb   
77                   163                   de   
78                   165                   fr   
79                   167                   us   
80                   171             

### Types of RIS

Examine the count of different RIS types (e.g., Pure, Eprints, Fedora etc).

In [2]:
''' Table of count of RIS types'''
vals = df_all_data.groupby("repository_metadata_software_name").size().sort_values(ascending=False)
display(vals)


repository_metadata_software_name
dspace             2035
other               537
eprints             537
weko                530
digital_commons     291
islandora           151
opus                 87
contentdm            78
hal                  66
pure                 60
dlibra               55
fedora               50
greenstone           28
drupal               27
invenio              23
wildfire             22
diva_portal          19
earmas               14
digitool             14
vital                12
mycore               11
samvera              10
digibib              10
omeka                 9
fez                   9
xoonips               7
dspace_cris           7
cybertesis            6
open_repository       4
equella               3
scielo                1
dtype: int64

&NewLine;  

This contains a lot of 'other' values, but `repository_metadata_software_name` can be used to replace the 'other' value for something more specific.

In [3]:
display(df_all_data["repository_metadata_software_name"])

df_all_data.loc[df_all_data.repository_metadata_software_name == 'other', 'repository_metadata_software_name'] = df_all_data.repository_metadata_software_name_other


0               eprints
1               eprints
2               eprints
3                   NaN
4                   hal
5               eprints
6                  opus
7                dspace
8                dspace
9                dspace
10                  NaN
11              eprints
12                other
13              eprints
14              eprints
15                other
16              eprints
17                other
18                  hal
19                  hal
20               drupal
21              eprints
22              eprints
23                  NaN
24               dspace
25               dspace
26                other
27               dspace
28          diva_portal
29               drupal
30                  hal
31                 pure
32                other
33                other
34                other
35               dspace
36                other
37                other
38             digitool
39                other
40                other
41              

Some cells contain the same data, but in slightly different formats (e.g., 

In [4]:
df_all_data['repository_metadata_software_name'] = df_all_data['repository_metadata_software_name'].str.replace('_', ' ')
df_all_data['repository_metadata_software_name'] = df_all_data['repository_metadata_software_name'].str.replace('-', ' ')
display(df_all_data['repository_metadata_software_name'])

0                                        eprints
1                                        eprints
2                                        eprints
3                                            NaN
4                                            hal
5                                        eprints
6                                           opus
7                                         dspace
8                                         dspace
9                                         dspace
10                                           NaN
11                                       eprints
12                            CDSWare and Apache
13                                       eprints
14                                       eprints
15                                          HTML
16                                       eprints
17                                        Cocoon
18                                           hal
19                                           hal
20                  

We can now redo the table with better detail, including ignoring case to better group values.

In [5]:
''' Table of count of RIS types'''
df_all_data["repository_metadata_software_name"] = df_all_data["repository_metadata_software_name"].str.lower()
vals = df_all_data.groupby("repository_metadata_software_name".lower()).size().sort_values(ascending=False)
display(vals)
#vals.to_csv('./vals.csv')

repository_metadata_software_name
dspace                                      2035
eprints                                      537
weko                                         530
digital commons                              435
islandora                                    151
opus                                          87
contentdm                                     78
hal                                           66
pure                                          60
dlibra                                        57
fedora                                        50
diva portal                                   31
greenstone                                    28
drupal                                        27
invenio                                       24
wildfire                                      22
html                                          17
open repository                               16
iris                                          16
digitool                           

We also see the following similar entries, which we want to merge into the same value.
`
cspace
cspace.

custom
custom software

dataverse
dataverse network

django
django/python

dkum
dkum   digital library platform from uni

dspace  
dspace cris

e cats
e cats library
e catslibrary
e catslibrary ver.6

figshare
figshare for institutions

iliswave j
iliswave j　e lib
iliswave j v3
iliswavej
ilisweb j  e lib
富士通　iliswave j
富士通 iliswave j

infolib
infolib asp
infolib dbr
infolibクラウドサービス

intranda
intranda viewer

mitos
mi̇tos

nalis r
nalis r(dspace)

omp
omp (open monograph press)

ori oai
ori oai 1.7

polaris by mysciencework
polaris os

pubman
pubman/inge

typo
typo3

visual library
visual library server
visual library software
`


In [115]:
print(df_all_data.columns)

Index(['system_metadata_id', 'organisation_country', 'organisation_url',
       'repository_metadata_software_name',
       'repository_metadata_metadata_record_count', 'repository_metadata_type',
       'repository_metadata_url', 'repository_metadata_full_text_record_count',
       'repository_metadata_oai_url', 'system_metadata_uri',
       'repository_metadata_software_name_other', 'country_name'],
      dtype='object')


In [117]:
# List of similar string values
similar_values = {
    'cspace.': 'cspace',
    'custom software': 'custom',
    'dataverse network': 'dataverse',
    'django/python': 'django',
    'dkum   digital library platform from uni': 'dkum',
    'dspace cris': 'dspace',
    'e cats library': 'e cats',
    'e catslibrary': 'e cats',
    'e catslibrary ver.6': 'e cats',
    'iliswave j　e lib': 'iliswave j',
    'iliswave j v3': 'iliswave j',
    'iliswavej': 'iliswave j',
    'ilisweb j  e lib': 'iliswave j',
    '富士通　iliswave j': 'iliswave j',
    '富士通 iliswave j': 'iliswave j',
    'infolib asp': 'infolib',
    'infolib dbr': 'infolib',
    'infolibクラウドサービス': 'infolib',
    'mi̇tos': 'mitos',
    'nalis r(dspace)': 'nalis r',
    'omp (open monograph press)': 'omp',
    'ori oai 1.7': 'ori oai',
    'polaris by mysciencework': 'polaris os',
    'pubman/inge': 'pubman',
    'typo3': 'typo',
    'visual library server': 'visual library',
    'visual library software': 'visual library'
}

def clean_string(value):
    for similar_value, cleaned_value in similar_values.items():
        if similar_value in value:
            return cleaned_value
    return value

vals = df_all_data['repository_metadata_software_name'].apply(clean_string)

#vals = df_all_data.groupby("repository_metadata_software_name".lower()).size().sort_values(ascending=False)
#vals.loc[vals["repository_metadata_software_name"] == 'typo3', 'repository_metadata_software_name'] == 'typo'
display(vals)

TypeError: argument of type 'float' is not iterable

and dump to latex if needed.

In [7]:
print(vals.to_latex())

\begin{tabular}{lr}
\toprule
{} &     0 \\
repository\_metadata\_software\_name        &       \\
\midrule
dspace                                   &  2035 \\
eprints                                  &   537 \\
weko                                     &   530 \\
digital commons                          &   435 \\
islandora                                &   151 \\
opus                                     &    87 \\
contentdm                                &    78 \\
hal                                      &    66 \\
pure                                     &    60 \\
dlibra                                   &    57 \\
fedora                                   &    50 \\
diva portal                              &    31 \\
greenstone                               &    28 \\
drupal                                   &    27 \\
invenio                                  &    24 \\
wildfire                                 &    22 \\
html                                     &    17 \\
open repo

/tmp/ipykernel_93435/2121909498.py:1: FutureWarning: In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.
  print(vals.to_latex())


In [8]:
df_all_data.to_csv('./all_data.csv')

## Counts per country

Convert the column with ISO country codes to regular names.

In [9]:
import country_converter as coco
df_all_data = df_all_data.assign(country_name = coco.convert(names=df_all_data['organisation_country'], to='name_short'))

In [10]:
''' Table of count of countries'''
country_count_table = df_all_data.groupby("country_name").size().sort_values(ascending=False)


In [11]:
country_count_table

country_name
United States                           754
Japan                                   656
United Kingdom                          247
Germany                                 247
Türkiye                                 155
Indonesia                               154
Peru                                    145
Croatia                                 142
Spain                                   126
Brazil                                  125
Italy                                   125
France                                  118
Poland                                  105
Ukraine                                  99
Colombia                                 92
Canada                                   85
India                                    84
Australia                                76
Norway                                   63
Taiwan                                   60
Argentina                                59
China                                    56
Netherlands        

In [12]:
print(country_count_table.to_latex())

\begin{tabular}{lr}
\toprule
{} &    0 \\
country\_name                         &      \\
\midrule
United States                        &  754 \\
Japan                                &  656 \\
United Kingdom                       &  247 \\
Germany                              &  247 \\
Türkiye                              &  155 \\
Indonesia                            &  154 \\
Peru                                 &  145 \\
Croatia                              &  142 \\
Spain                                &  126 \\
Brazil                               &  125 \\
Italy                                &  125 \\
France                               &  118 \\
Poland                               &  105 \\
Ukraine                              &   99 \\
Colombia                             &   92 \\
Canada                               &   85 \\
India                                &   84 \\
Australia                            &   76 \\
Norway                               &   63 \\
Taiwan  

/tmp/ipykernel_93435/331536426.py:1: FutureWarning: In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.
  print(country_count_table.to_latex())


In [13]:
df_ris_counts_per_country = df_all_data.groupby(["country_name","repository_metadata_software_name"])["repository_metadata_software_name"].count()
df_ris_counts_per_country

country_name                          repository_metadata_software_name       
Aland Islands                         eprints                                       1
Albania                               dspace                                        1
Algeria                               dspace                                       16
                                      eprints                                       1
                                      self build cms                                1
                                      wordpress                                     1
Andorra                               digital commons                               1
Argentina                             bdunco                                        1
                                      bespoke system                                1
                                      dspace                                       35
                                      eprints                

This gives a lot of low values, so we can get the top 3 RIS platforms by country.

In [111]:
#df_ris_counts_per_country_top3 = df_all_data.groupby(["country_name","repository_metadata_software_name"])['country_name'].count().reset_index(name="count")
#df_ris_counts_per_country_top3.nlargest(3, 'count')

grouped = df_all_data.groupby(['country_name', 'repository_metadata_software_name']).size().reset_index(name='count')
#display(grouped)
def get_top_three(group):
    # Sort the group by count in descending order
    sorted_group = group.sort_values(by='count', ascending=False)
    # Take the top three rows
    top_three = sorted_group.head(3)
    return top_three

top_three_per_country = grouped.groupby('country_name', as_index=False).apply(get_top_three).reset_index(drop=True)
top_three_per_country

country_name repository_metadata_software_name  \
0                           Aland Islands                           eprints   
1                                 Albania                            dspace   
2                                 Algeria                            dspace   
3                                 Algeria                           eprints   
4                                 Algeria                    self build cms   
5                                 Andorra                   digital commons   
6                               Argentina                            dspace   
7                               Argentina                        greenstone   
8                               Argentina                           eprints   
9                                 Armenia                           eprints   
10                                Armenia                        greenstone   
11                              Australia                            dspace   
12                              Australia                           eprints   
13                              Australia                   digital commons   
14                                Austria                           eprints   
15                                Austria                            fedora   
16                                Austria             visual library server   
17                             Azerbaijan                            dspace   
18                             Bangladesh                            dspace   
19                             Bangladesh                        greenstone   
20                                Belarus                            dspace   
21                                Belarus                        perl based   
22                                Belgium                            dspace   
23                                Belgium                              doks   
24                                Belgium                            drupal   
25                                Bolivia                        cybertesis   
26                                Bolivia                            dspace   
27                 Bosnia and Herzegovina                            fedora   
28                               Botswana                            dspace   
29                                 Brazil                            dspace   
30                                 Brazil                            drupal   
31                                 Brazil                              tede   
32                               Bulgaria                            dspace   
33                               Bulgaria                           eprints   
34                             Cabo Verde                            dspace   
35                                 Canada                            dspace   
36                                 Canada                           eprints   
37                                 Canada                   digital commons   
38                                  Chile                            dspace   
39                                  Chile                        cybertesis   
40                                  Chile       ohs (open harvester system)   
41                                  China                            dspace   
42                                  China                            cspace   
43                                  China                           cspace.   
44                               Colombia                            dspace   
45                               Colombia                           eprints   
46                               Colombia                         contentdm   
47                             Costa Rica                            dspace   
48                                Croatia                         islandora   
49                                Croatia                           eprints   


### RIS per continent

We can also add continents to the dataset, based on country.

In [ ]:
df_all_data = df_all_data.assign(continent = coco.convert(names=df_all_data['organisation_country'], to='continent'))

In [ ]:
continent_count_table = df_all_data.groupby("continent").size().sort_values(ascending=False)

In [ ]:
continent_count_table

In [ ]:
print(continent_count_table.to_latex())

In [ ]:
df_counts_per_continent = df_all_data.groupby(["continent","repository_metadata_software_name"])["country_name"].count()

In [ ]:
display(df_counts_per_continent)

In [ ]:
df_all_data.keys()

Get a list of all urls per RIS type

In [ ]:
df_urls_per_ris = df_all_data.groupby("repository_metadata_software_name")["repository_metadata_url"].apply(list).reset_index(name='urls')

In [ ]:
df_urls_per_ris.set_index('repository_metadata_software_name')

Get a list of urls per RIS type

In [ ]:
for ris in df_urls_per_ris.iterrows():
    print(ris[1][0])
    print(ris[1][1])